In [18]:
!git clone https://github.com/guo-research-group/AD-Ray-Optics

Cloning into 'AD-Ray-Optics'...
remote: Enumerating objects: 453, done.
remote: Counting objects: 100% (128/128), done.
remote: Compressing objects: 100% (113/113), done.
remote: Total 453 (delta 55), reused 42 (delta 13), pack-reused 325
Receiving objects: 100% (453/453), 1.65 MiB | 9.31 MiB/s, done.
Resolving deltas: 100% (133/133), done.


In [19]:
%cd /content/AD-Ray-Optics
!python setup.py develop

/content/AD-Ray-Optics
running develop
/usr/local/lib/python3.10/dist-packages/setuptools/command/develop.py:40: EasyInstallDeprecationWarning: easy_install command is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` and ``easy_install``.
        Instead, use pypa/build, pypa/installer, pypa/build or
        other standards-based tools.

        See https://github.com/pypa/setuptools/issues/917 for details.
        ********************************************************************************

!!
  easy_install.initialize_options(self)
/usr/local/lib/python3.10/dist-packages/setuptools/_distutils/cmd.py:66: SetuptoolsDeprecationWarning: setup.py install is deprecated.
!!

        ********************************************************************************
        Please avoid running ``setup.py`` directly.
        Instead, use pypa/build, pypa/installer, pypa/build or
        other s

In [20]:
pip install -r requirements.txt

In [1]:
from rayoptics import *

In [2]:
from rayoptics.environment import *
from rayoptics.mpl.interactivediagram import InteractiveDiagram


In [3]:
import jax.numpy as jnp
from jax import grad, jit, vmap
from jax import random

In [4]:
from rayoptics.environment import *
import random
from copy import deepcopy
from scipy.optimize import minimize
import numpy as np

In [5]:
import jax
import jax.numpy as jnp
from jax import grad, jit, vmap
from jax.numpy import sqrt, copysign, sin
jax.config.update("jax_enable_x64", True)

In [6]:
from jax import lax

In [7]:
isdark = False

In [18]:
from visualize.rays import visualize_rays
from visualize.lens import visualize_lens
import plotly.graph_objects as go

# Jose Sasian’s Lens Design OPTI 517 EXAMPLE
# create a new optical model and set up aliases
opm = OpticalModel()
sm  = opm['seq_model']
osp = opm['optical_spec']
pm = opm['parax_model']
em = opm['ele_model']
pt = opm['part_tree']
ar = opm['analysis_results']

# define field specs
osp['pupil'] = PupilSpec(osp, key=['object', 'pupil'], value=12.5)
osp['fov'] = FieldSpec(osp, key=['object', 'angle'], value=20, flds=[0, 0.707, 1], is_relative=True)
osp['wvls'] = WvlSpec([('F', 0.5), (587.5618, 1.0), ('C', 0.5)], ref_wl=1)
wv = 587.5618

# define interface and gap data
opm.radius_mode = True
sm.gaps[0].thi= 15

# add the surfaces
sm.add_surface([23.713, 4.831, 'N-LAK9', 'Schott'])
sm.add_surface([7331.288, 5.86])
sm.add_surface([-24.456, .975, 'N-SF5,Schott'])
sm.set_stop()
sm.add_surface([21.896, 4.822])
sm.add_surface([86.759, 3.127, 'N-LAK9', 'Schott'])
sm.add_surface([-20.4942, 41.2365])

# update the model
opm.update_model()

# set visualization parameters
radius = 8
rays = 15
x_offsets = list(np.linspace(-radius, radius, rays))
y_offsets = list(np.linspace(-radius, radius, rays))
z_offsets = [0] * rays
num_rays = 1

ray_data = visualize_rays(sm, radius=radius*0.9, wv=wv, x_offsets=x_offsets, y_offsets=y_offsets, num_rays=num_rays)
lens_data = visualize_lens(sm, radius=radius)

# plot
data = []
data.extend(ray_data)
data.extend(lens_data)
fig = go.Figure(data = data)
fig.update_scenes(aspectmode='data')
fig.show()